In [1]:
import pandas as pd
import matplotlib.pyplot as plt
import pandas_datareader as pdr
from urllib import urlopen
from bs4 import BeautifulSoup
import os
import requests
import json
import pickle
from pandas.tseries.offsets import BDay
import datetime as dt
'''this program will take around an hour to run'''

'this program will take around an hour to run'

In [6]:
no_hist_symbol = []

def save_sp500_tickers():
    resp = requests.get('http://en.wikipedia.org/wiki/List_of_S%26P_500_companies')
    soup = BeautifulSoup(resp.text, 'lxml')
    table = soup.find('table', {'class': 'wikitable sortable'})
    tickers = []
    for row in table.findAll('tr')[1:]:
        ticker = row.findAll('td')[0].text
        tickers.append(ticker)      
    with open("sp500tickers.pickle","wb") as f:
        pickle.dump(tickers,f)    
    return tickers    

def select_ticker(tick):
    url = 'https://finance.yahoo.com/quote/{0}/analysts?p={0}'
    return url.format(tick)

def yahoo_finance_analyst_data(url):
    req = urlopen(url)
    raw = req.read()
    soup = BeautifulSoup(raw,'lxml')
    return soup

def auto_symbols(ticker):
    url = select_ticker(ticker)
    return url

def grab_dict(soup):
    l = [i for i in soup.find_all('script')]
    mylist = [str(item) for item in l]
    m = max(mylist,key=len)
    ind = mylist.index(m)
    data = l[mylist.index(m)]
    data_dict = data.text[112:-12]
    all_tables = json.loads(data_dict)
    return all_tables

def upgrade_downgrade_pandas(dic,tick):
    try:
        stock_upgrade_downgrade_history = dic['context']['dispatcher']['stores']['QuoteSummaryStore']['upgradeDowngradeHistory']['history']
        pd_stock_upgrade_downgrade_history = pd.DataFrame(stock_upgrade_downgrade_history)
        pd_stock_upgrade_downgrade_history['epochGradeDate'] = pd.to_datetime(pd_stock_upgrade_downgrade_history['epochGradeDate'],unit='s')
        pd_stock_upgrade_downgrade_history.columns.values[1] = 'date'
        pd_stock_upgrade_downgrade_history.insert(0,'stockTicker',tick)
        return pd_stock_upgrade_downgrade_history
    except Exception:
        print "error" + tick
        no_hist_symbol.append(tick)
        

def single_company_hist(tick):
    url = select_ticker(tick)
    soup = yahoo_finance_analyst_data(url)
    full_dict = grab_dict(soup)
    return upgrade_downgrade_pandas(full_dict,tick)

def list_of_all_stock_grading_history(good_list):
    
    all_stock_grading_history = []
    for ticker in good_list:
        if ticker not in no_hist_symbol:
            url = auto_symbols(ticker)
            soup = yahoo_finance_analyst_data(url)
            all_tables = grab_dict(soup)
            grading_history = upgrade_downgrade_pandas(all_tables,ticker)
            all_stock_grading_history.append(grading_history)
    concat_lists_to_pd = pd.concat(all_stock_grading_history)
    return concat_lists_to_pd

def all_hist_to_tick(df):
    list_of_stock_histories = []
    for ticker in df['stockTicker'].unique():
        try:
            stock_df = pdr.get_data_yahoo(symbols=ticker, start=df.loc[df['stockTicker']==ticker].date.iloc[-1])
            stock_df['stockTicker'] = ticker
            stock_df.reset_index(inplace = True)
            stock_df['Percent_change'] =  stock_df.Close.pct_change()
            list_of_stock_histories.append(stock_df)
            print ticker
        except Exception: 
            print 'error @ ' + ticker
    concat_lists_to_pd = pd.concat(list_of_stock_histories)
    return concat_lists_to_pd

def combine_toGrade(df):
    
    Strong_Buy = ['Outperform','Mkt Outperformer','Recomm List','Market Outperform','Mkt Outperform','NT Strong Buy','Recommended List','LT Accumulate','Outperformer','Top Pick', 'Strong Buy','Outperf. Signif.','Sector Outperform','Conviction Buy']
    Buy = ['Buy','Overweight','Trading Buy','NT Accum/LT Buy', 'NT Ntrl/LT Buy','Long-Term Buy','Above Average','LT Attractive','LT Accum','LT Buy','Accumulate','NT Accum','NT Nuet/ LT Buy','Attractive','Positive','Long-term Buy','Add','NT Buy']
    Hold = ['Hold','Neutral','Peer perform','Equal-weight','Perform-In-Line','Perform In Line','In-line','Market Perform','Mkt Performer','Average','NT Neutral','Maintain Position','ST Neutral','Sector Perform','Mixed','Market Weight','Equal-weight','Perform','Sector Weight','Peer Perform','In-Line','Fair Value','Mkt Perform','Equal Weight']
    Underperform = ['Underperform', 'Underperformer','Below Average','Unattractive','Market Underperform','Cautious','Mkt Underperform','Sector Underperform']
    Sell = ['Sell','Underweight','Reduce','Negative','Trim']

    list_dict = {
    'Strong_buy':Strong_Buy,
    'Buy':Buy,
    'Hold':Hold,
    'Underperform':Underperform,
    'Sell':Sell
    }
    reversed_dict = {val: key for key in list_dict for val in list_dict[key]}
    df['toGrade_combined'] = df['toGrade'].map(reversed_dict)
    df['fromGrade_combined'] = df['fromGrade'].map(reversed_dict)
    return df

#symbols=['SPY']



def get_stock_data(symbols):
    for symbol in symbols:
        print symbol
        df_temp =  pdr.get_data_yahoo(symbols=symbol)
        df_temp = df_temp.rename(columns={'Adj Close':symbol})
        return df_temp

def use_only_spy_dates(spy,df):
    df_list = []
    for symbol in df.stockTicker.unique():
        dates = pd.DataFrame(index=spy)
        temp_df=df.loc[df['stockTicker'] == symbol]
        dates = dates.join(temp_df)
        df_list.append(dates)
    return pd.concat(df_list)

def dir_to_path(path,base_dir='firm_grades'):
    return os.path.join(base_dir,'{}'.format(path))  

def make_dir(path):
    if not os.path.exists(path):
        return os.mkdirs(path)


def dir_to_symbol(symbol,base_dir):
    return os.path.join(base_dir,'{}.csv'.format(symbol))  




def channel_dirs(df,path='firm_grades'):
    df = df.set_index('Date')
    df_cols = df[['stockTicker', 'Adj Close']]
    make_dir(path)
    for firm in df.firm.unique():
        print firm
        df_temp = df.loc[df['firm']==firm]
        firm_path = dir_to_path(firm,path)
        make_dir(path)
        for grade in df_temp.toGrade_combined.unique():
            print grade
            grade_df = df_temp.loc[df_temp[toGrade_combined]==grade]
            grade_path = dir_to_path(grade,firm_path)
            make_dir(path)
            for symbol in grade_df.stockTicker.unique():
                print symbol
                symb_df = df_cols.loc[df_cols['stockTicker']==symbol]
                grade_symb_df = grade_df.loc[grade_df['stockTicker']==symbol]
                df_joined = symb_df.join(grade_symb_df)
                df_joined.to_csv(dir_to_symbol(symbol,grade_path))
            
            





def merge_on_spy_dates(df,dates):
    '''
    makes folder called 'firm_grades'
    '''
    firms = []
    if not os.path.exists('firm_grades'):
        os.makedirs('firm_grades')
    '''
    1) checks dataframe for unique values of firm, creates path and cds to firm_grades/'firm'
    2) creates separate dataframe for all instances of firm upgrades
    '''
    for firm in df['firm'].unique():
        path = firm_to_dir(firm,base_dir='firm_grades')
        
        if not os.path.exists(path):
            os.makedirs(path)
        df1 = df.loc[df['firm']==firm]
        '''
        1)start an empty list
        2)for each of the stock tickers in the firm df
        3)in the path of firm_grade/'firm'/
        4)locate all of the unique values of the stocktickers that the
        firm upgraded or downgraded
        5)go to the main large db and locate all data for that symbol
        '''
        temp_list = []
        for symbol in df1['stockTicker'].unique():
            temp_path=dir_to_symbol(symbol,base_dir=path)
            temp_df = df1.loc[df1['stockTicker']==symbol]
            dates_df = dates.loc[dates['stockTicker']==symbol]

            #df_dates = df_dates.join(temp_df)
            dates_df=dates_df.set_index(['stockTicker','Adj Close'],append=True).join(temp_df.set_index(['stockTicker','Adj Close'],append=True)).reset_index(level=['stockTicker','Adj Close'])
            dates_df.to_csv(temp_path)
            temp_list.append(dates_df)
        firms.append(pd.concat(temp_list))
        print firm
    return pd.concat(firms)
        
            
            
            
#             os.chdir(temp_path)
#             for grade in temp_df['toGrade_combined'].unique():
#                 if not os.path.exists(grade):
#                     os.makedirs(grade)
#                     temp_path2 = os.chdir(grade)
#                     dates_df = temp_df.loc['toGrade_combined'.notnull()]
#                     start_date = 
#                     end_date = 
#                     for date in temp_df2.Date:
#                         if date <= start_date:
#                             begin_date = date-30    
#                         else:
#                             begin_date = '1/4/2010'
                        
#                         if date >= end_date:
#                             last_date = date+90
#                         else:
#                             last_date = end_date
                            
                        
                        
                        
                        
                
            #df_dates = df_dates.join(temp_df)
            dates_df=dates_df.set_index(['stockTicker','Adj Close'],append=True).join(temp_df.set_index(['stockTicker','Adj Close'],append=True)).reset_index(level=['stockTicker','Adj Close'])
            dates_df.to_csv(temp_path)
            temp_list.append(dates_df)
        firms.append(pd.concat(temp_list))
        print firm
    return pd.concat(firms)
        



if __name__=='__main__':
    print "get snp500 stock tickers\n"
    snp500tickers = save_sp500_tickers()
    print "use tickers to grab stock upgrade downgrade history\n"
    stock_to_grade = list_of_all_stock_grading_history(snp500tickers)
    print "use tickers to grab all stock price data\n"
    all_snp_price_hist = all_hist_to_tick(stock_to_grade)
    print "combine like-terms of grading into a minimalized list\n"
    stock_to_grade = combine_toGrade(stock_to_grade)
    
    #make copies of dataframes
    stock_to_grade_copy = stock_to_grade.copy()
    all_snp_price_hist_copy = all_snp_price_hist.copy()
    spy_stock_hist_data = all_snp_price_hist.copy()
    
    #remove unneeded columns from the dataframes
    spy_stock_hist_data = spy_stock_hist_data[['Date','stockTicker','Adj Close']]
    stock_to_grade_copy = stock_to_grade_copy[['date','stockTicker','firm','toGrade_combined']]
    all_snp_price_hist_copy = all_snp_price_hist_copy[['Date', 'Adj Close','stockTicker']]
    
    #set the Date as index
    stock_to_grade_copy=stock_to_grade_copy.set_index('date')
    stock_to_grade_copy.index.names=['Date']
    all_snp_price_hist_copy=all_snp_price_hist_copy.set_index('Date')
    
    #change the date index to datetime object
    all_snp_price_hist_copy.index.to_datetime()
    stock_to_grade_copy.index.to_datetime()
    
    print "merge grading df and price df on Date and stockTicker\n"
    stock_price_merge_grade = stock_to_grade_copy.set_index('stockTicker',append=True).join(all_snp_price_hist_copy.set_index('stockTicker',append=True)).reset_index(level='stockTicker')
    #rearange order of columns
    cols = ['Adj Close','stockTicker','firm','toGrade_combined']
    stock_price_merge_grade = stock_price_merge_grade[cols]
    
    print "grab dates of SPY stock ticker to serve as a constant\n"
    spy_dates = get_stock_data(['SPY']).index
    spy_dates_symb = use_only_spy_dates(spy_dates,all_snp_price_hist_copy)
    
    print "create a concatenated joined dataframe for each firms upgrade and downgrade history with stockTicker prices before and after included\n"
    print "this step will take around 20 minutes"
    dfs = channel_dirs()
    #final_df = merge_on_spy_dates(stock_price_merge_grade,spy_dates_symb)
    
    print "write to csv titled: snp500finaldf.csv" 
    final_df.to_csv("snp500finaldf.csv")

get snp500 stock tickers

use tickers to grab stock upgrade downgrade history

errorBRK.B
errorBF.B
errorDISCK
use tickers to grab all stock price data

MMM
ABT
ABBV
ACN
ATVI
AYI
ADBE
AMD
AAP
AES
AET
AMG
AFL
A
APD
AKAM
ALK
ALB
ARE
ALXN
ALGN
ALLE
AGN
ADS
LNT
ALL
GOOGL
GOOG
MO
AMZN
AEE
AAL
AEP
AXP
AIG
AMT
AWK
AMP
ABC
AME
AMGN
APH
APC
ADI
ANDV
ANSS
ANTM
AON
AOS
APA
AIV
AAPL
AMAT
APTV
ADM
ARNC
AJG
AIZ
T
ADSK
ADP
AZO
AVB
AVY
BHGE
BLL
BAC
BK
BAX
BBT
BDX
BBY
BIIB
BLK
HRB
BA
BWA
BXP
BSX
BHF
BMY
AVGO
CHRW
CA
COG
CDNS
CPB
COF
CAH
CBOE
KMX
CCL
CAT
CBG
CBS
CELG
CNC
CNP
CTL
CERN
CF
SCHW
CHTR
CHK
CVX
CMG
CB
CHD
CI
XEC
CINF
CTAS
CSCO
C
CFG
CTXS
CLX
CME
CMS
KO
CTSH
CL
CMCSA
CMA
CAG
CXO
COP
ED
STZ
COO
GLW
COST
COTY
CCI
CSRA
CSX
CMI
CVS
DHI
DHR
DRI
DVA
DE
DAL
XRAY
DVN
DLR
DFS
DISCA
DISH
DG
DLTR
D
DOV
DWDP
DPS
DTE
DRE
DUK
DXC
ETFC
EMN
ETN
EBAY
ECL
EIX
EW
EA
EMR
ETR
EVHC
EOG
EQT
EFX
EQIX
EQR
ESS
EL
ES
RE
EXC
EXPE
EXPD
ESRX
EXR
XOM
FFIV
FB
FAST
FRT
FDX
FIS
FITB
FE
FISV
FLIR
FLS
FLR
FMC
FL
F
FTV
FBHS
BEN
FC

WindowsError: [Error 3] The system cannot find the path specified: 'firm_grades\\KeyBanc Capital Mkts / McDonald'

In [ ]:
if __name__=='__main__':
    print "get snp500 stock tickers\n"
    snp500tickers = save_sp500_tickers()
    print "use tickers to grab stock upgrade downgrade history\n"
    stock_to_grade = list_of_all_stock_grading_history(snp500tickers)
    print "use tickers to grab all stock price data\n"
    all_snp_price_hist = all_hist_to_tick(stock_to_grade)
    print "combine like-terms of grading into a minimalized list\n"
    stock_to_grade = combine_toGrade(stock_to_grade)
    
    #make copies of dataframes
    stock_to_grade_copy = stock_to_grade.copy()
    all_snp_price_hist_copy = all_snp_price_hist.copy()
    spy_stock_hist_data = all_snp_price_hist.copy()
    
    #remove unneeded columns from the dataframes
    spy_stock_hist_data = spy_stock_hist_data[['Date','stockTicker','Adj Close']]
    stock_to_grade_copy = stock_to_grade_copy[['date','stockTicker','firm','toGrade_combined']]
    all_snp_price_hist_copy = all_snp_price_hist_copy[['Date', 'Adj Close','stockTicker']]
    
    #set the Date as index
    stock_to_grade_copy=stock_to_grade_copy.set_index('date')
    stock_to_grade_copy.index.names=['Date']
    all_snp_price_hist_copy=all_snp_price_hist_copy.set_index('Date')
    
    #change the date index to datetime object
    all_snp_price_hist_copy.index.to_datetime()
    stock_to_grade_copy.index.to_datetime()
    
    print "merge grading df and price df on Date and stockTicker\n"
    stock_price_merge_grade = stock_to_grade_copy.set_index('stockTicker',append=True).join(all_snp_price_hist_copy.set_index('stockTicker',append=True)).reset_index(level='stockTicker')
    #rearange order of columns
    cols = ['Adj Close','stockTicker','firm','toGrade_combined']
    stock_price_merge_grade = stock_price_merge_grade[cols]
    
    print "grab dates of SPY stock ticker to serve as a constant\n"
    spy_dates = get_stock_data(['SPY']).index
    spy_dates_symb = use_only_spy_dates(spy_dates,all_snp_price_hist_copy)
    
    print "create a concatenated joined dataframe for each firms upgrade and downgrade history with stockTicker prices before and after included\n"
    print "this step will take around 20 minutes"
    dfs = channel_dirs()
    #final_df = merge_on_spy_dates(stock_price_merge_grade,spy_dates_symb)
    
    print "write to csv titled: snp500finaldf.csv" 
    final_df.to_csv("snp500finaldf.csv")

In [2]:
df1 = pd.read_csv("snp500finaldf.csv")
df1 = df1.set_index('Date')
#df1 = df1.set_index(['stockTicker','Adj Close'])

In [3]:
def dir_to_path(path,base_dir='firm_grades'):
    return os.path.join(base_dir,'{}'.format(path))  

def make_dir(path):
    if not os.path.exists(path):
        return os.mkdir(path)


def dir_to_symbol(symbol,base_dir):
    return os.path.join(base_dir,'{}.csv'.format(symbol))  


In [128]:
def channel_dirs(df,path='firm_grades'):
    df_cols = df[['stockTicker', 'Adj Close']]
    make_dir(path)
    for firm in df.firm.unique():
        df_temp = df.loc[df['firm']==firm]
        firm_path = dir_to_path(firm,path)
        make_dir(firm_path)
        for grade in df_temp.toGrade_combined.unique():
            grade_df = df_temp.loc[df_temp['toGrade_combined']==grade]
            grade_path = dir_to_path(grade,firm_path)
            make_dir(grade_path)
            for symbol in grade_df.stockTicker.unique():
                symb_df = df_cols.loc[df_cols['stockTicker']==symbol].set_index(['stockTicker','Adj Close'],append=True)
                grade_symb_df = grade_df.loc[grade_df['stockTicker']==symbol].set_index(['stockTicker','Adj Close'],append=True)
                grade_symb_df_date_index = grade_symb_df.reset_index().drop_duplicates().set_index('Date')
                grade_symb_df_date_index.index = pd.to_datetime(grade_symb_df_date_index.index).date
                grade_symb_df_combined = symb_df.join(grade_symb_df).reset_index().drop_duplicates().set_index('Date')
                for date in grade_symb_df_date_index.index.values:
                    start_date = date
                    bus90str = str(start_date+BDay(90))[:-9]
                    bus90 = dt.datetime.strptime(bus90str,'%Y-%m-%d').date()
                    end_date = bus90
                    grade_symb_df_combined.index = pd.to_datetime(grade_symb_df_combined.index).date
                    if end_date in grade_symb_df_combined.index.values:
                        temp_df = grade_symb_df_combined.copy()
                        start = temp_df.index.searchsorted(start_date)
                        end = temp_df.index.searchsorted(end_date)
                    temp = temp_df[start:end]
                    f_path = dir_to_symbol(symbol+str(start),grade_path)
                    print temp
                    temp.to_csv(f_path)


In [ ]:
channel_dirs(df1,path='firm_grades')

           stockTicker  Adj Close           firm toGrade_combined
2012-02-08         YUM  40.608948  Goldman Sachs             Hold
2012-02-09         YUM  40.905125            NaN              NaN
2012-02-10         YUM  40.798008            NaN              NaN
2012-02-13         YUM  40.697174            NaN              NaN
2012-02-14         YUM  40.319065            NaN              NaN
2012-02-15         YUM  40.155228            NaN              NaN
2012-02-16         YUM  40.791695            NaN              NaN
2012-02-17         YUM  41.119396            NaN              NaN
2012-02-21         YUM  41.276947            NaN              NaN
2012-02-22         YUM  41.529018            NaN              NaN
2012-02-23         YUM  41.484909            NaN              NaN
2012-02-24         YUM  41.302151            NaN              NaN
2012-02-27         YUM  41.314754            NaN              NaN
2012-02-28         YUM  41.566826            NaN              NaN
2012-02-29

           stockTicker  Adj Close           firm toGrade_combined
2013-05-20         EFX  58.740429  Goldman Sachs             Hold
2013-05-21         EFX  59.108257            NaN              NaN
2013-05-22         EFX  58.303741            NaN              NaN
2013-05-23         EFX  57.915691            NaN              NaN
2013-05-24         EFX  57.934620            NaN              NaN
2013-05-28         EFX  58.360535            NaN              NaN
2013-05-29         EFX  58.171242            NaN              NaN
2013-05-30         EFX  58.360535            NaN              NaN
2013-05-31         EFX  57.641209            NaN              NaN
2013-06-03         EFX  58.010334            NaN              NaN
2013-06-04         EFX  57.660133            NaN              NaN
2013-06-05         EFX  56.590607            NaN              NaN
2013-06-06         EFX  56.600063            NaN              NaN
2013-06-07         EFX  57.120636            NaN              NaN
2013-06-10

           stockTicker  Adj Close           firm toGrade_combined
2012-02-13          HP  48.449226  Goldman Sachs             Hold
2012-02-14          HP  48.269516            NaN              NaN
2012-02-15          HP  48.057117            NaN              NaN
2012-02-16          HP  49.274277            NaN              NaN
2012-02-17          HP  51.692238            NaN              NaN
2012-02-21          HP  50.875362            NaN              NaN
2012-02-22          HP  51.545200            NaN              NaN
2012-02-23          HP  51.218456            NaN              NaN
2012-02-24          HP  51.234791            NaN              NaN
2012-02-27          HP  50.777336            NaN              NaN
2012-02-28          HP  50.132008            NaN              NaN
2012-02-29          HP  50.074825            NaN              NaN
2012-03-01          HP  50.957047            NaN              NaN
2012-03-02          HP  49.641869            NaN              NaN
2012-03-05

           stockTicker  Adj Close           firm toGrade_combined
2013-06-20         DIS  57.938599  Goldman Sachs             Hold
2013-06-21         DIS  58.639698            NaN              NaN
2013-06-24         DIS  58.368603            NaN              NaN
2013-06-25         DIS  58.490128            NaN              NaN
2013-06-26         DIS  59.088398            NaN              NaN
2013-06-27         DIS  59.565144            NaN              NaN
2013-06-28         DIS  59.032314            NaN              NaN
2013-07-01         DIS  59.761452            NaN              NaN
2013-07-02         DIS  59.135139            NaN              NaN
2013-07-03         DIS  59.462315            NaN              NaN
2013-07-05         DIS  59.658623            NaN              NaN
2013-07-08         DIS  60.490589            NaN              NaN
2013-07-09         DIS  60.705593            NaN              NaN
2013-07-10         DIS  60.677547            NaN              NaN
2013-07-11

           stockTicker  Adj Close           firm toGrade_combined
2013-06-21        NWSA  15.007938  Goldman Sachs             Hold
2013-06-24        NWSA  14.921465            NaN              NaN
2013-06-25        NWSA  15.104020            NaN              NaN
2013-06-26        NWSA  14.796558            NaN              NaN
2013-06-27        NWSA  14.892641            NaN              NaN
2013-06-28        NWSA  14.652435            NaN              NaN
2013-07-01        NWSA  14.210463            NaN              NaN
2013-07-02        NWSA  14.412233            NaN              NaN
2013-07-03        NWSA  14.287327            NaN              NaN
2013-07-05        NWSA  15.046371            NaN              NaN
2013-07-08        NWSA  15.334616            NaN              NaN
2013-07-09        NWSA  15.094412            NaN              NaN
2013-07-10        NWSA  14.786951            NaN              NaN
2013-07-11        NWSA  14.537140            NaN              NaN
2013-07-12

...

           stockTicker  Adj Close       firm toGrade_combined
2015-05-28         OXY  68.798920  JP Morgan              Buy
2015-05-29         OXY  69.206062        NaN              NaN
2015-06-01         OXY  69.825630        NaN              NaN
2015-06-02         OXY  70.312447        NaN              NaN
2015-06-03         OXY  69.365379        NaN              NaN
2015-06-04         OXY  68.418335        NaN              NaN
2015-06-05         OXY  70.002670        NaN              NaN
2015-06-08         OXY  69.011917        NaN              NaN
2015-06-09         OXY  69.235321        NaN              NaN
2015-06-10         OXY  70.441666        NaN              NaN
2015-06-11         OXY  70.495270        NaN              NaN
2015-06-12         OXY  69.503380        NaN              NaN
2015-06-15         OXY  69.208496        NaN              NaN
2015-06-16         OXY  70.155708        NaN              NaN
2015-06-17         OXY  70.414848        NaN              NaN
2015-06-

           stockTicker  Adj Close       firm toGrade_combined
2015-06-05         AES  11.764437  JP Morgan              Buy
2015-06-08         AES  11.701814        NaN              NaN
2015-06-09         AES  12.086507        NaN              NaN
2015-06-10         AES  11.916526        NaN              NaN
2015-06-11         AES  12.095451        NaN              NaN
2015-06-12         AES  11.943364        NaN              NaN
2015-06-15         AES  12.023882        NaN              NaN
2015-06-16         AES  12.149129        NaN              NaN
2015-06-17         AES  12.229647        NaN              NaN
2015-06-18         AES  12.390681        NaN              NaN
2015-06-19         AES  12.390681        NaN              NaN
2015-06-22         AES  12.471199        NaN              NaN
2015-06-23         AES  12.265431        NaN              NaN
2015-06-24         AES  12.202808        NaN              NaN
2015-06-25         AES  12.104399        NaN              NaN
2015-06-

           stockTicker   Adj Close       firm toGrade_combined
2015-07-14         LMT  185.932907  JP Morgan              Buy
2015-07-15         LMT  186.269180        NaN              NaN
2015-07-16         LMT  188.333542        NaN              NaN
2015-07-17         LMT  187.922531        NaN              NaN
2015-07-20         LMT  191.612259        NaN              NaN
2015-07-21         LMT  189.762726        NaN              NaN
2015-07-22         LMT  189.426437        NaN              NaN
2015-07-23         LMT  189.463806        NaN              NaN
2015-07-24         LMT  187.791748        NaN              NaN
2015-07-27         LMT  187.913177        NaN              NaN
2015-07-28         LMT  190.211121        NaN              NaN
2015-07-29         LMT  194.433228        NaN              NaN
2015-07-30         LMT  192.863937        NaN              NaN
2015-07-31         LMT  193.452454        NaN              NaN
2015-08-03         LMT  194.096954        NaN          

           stockTicker  Adj Close       firm toGrade_combined
2015-09-08        MCHP  42.202492  JP Morgan              Buy
2015-09-09        MCHP  42.077312        NaN              NaN
2015-09-10        MCHP  41.916100        NaN              NaN
2015-09-11        MCHP  41.622120        NaN              NaN
2015-09-14        MCHP  41.650562        NaN              NaN
2015-09-15        MCHP  41.735909        NaN              NaN
2015-09-16        MCHP  41.641075        NaN              NaN
2015-09-17        MCHP  41.091057        NaN              NaN
2015-09-18        MCHP  40.588440        NaN              NaN
2015-09-21        MCHP  40.522057        NaN              NaN
2015-09-22        MCHP  39.820297        NaN              NaN
2015-09-23        MCHP  39.213360        NaN              NaN
2015-09-24        MCHP  39.146976        NaN              NaN
2015-09-25        MCHP  39.241810        NaN              NaN
2015-09-28        MCHP  38.748684        NaN              NaN
2015-09-

           stockTicker  Adj Close       firm toGrade_combined
2016-12-16         PEG  42.397621  JP Morgan              Buy
2016-12-19         PEG  42.089207        NaN              NaN
2016-12-20         PEG  42.185585        NaN              NaN
2016-12-21         PEG  42.012100        NaN              NaN
2016-12-22         PEG  42.098846        NaN              NaN
2016-12-23         PEG  42.098846        NaN              NaN
2016-12-27         PEG  42.214500        NaN              NaN
2016-12-28         PEG  41.838615        NaN              NaN
2016-12-29         PEG  42.455452        NaN              NaN
2016-12-30         PEG  42.291607        NaN              NaN
2017-01-03         PEG  41.819340        NaN              NaN
2017-01-04         PEG  42.108482        NaN              NaN
2017-01-05         PEG  42.175945        NaN              NaN
2017-01-06         PEG  42.600021        NaN              NaN
2017-01-09         PEG  41.944633        NaN              NaN
2017-01-